In [128]:
import sys
import requests
import json
import pandas as pd
import numpy as np
from tqdm import tqdm
import datetime
import dateutil.parser as parser
import time
import pickle
from flatten_json import flatten

In [3]:
API_KEY = 'v2wsp3yB5OWqhGf99uzEpFaGwddFnyCh'

In [10]:
start = datetime.datetime.strptime("01-1851", "%m-%Y")
start.month

1

In [63]:
instance1 = datetime.datetime.now()

In [64]:
instance2 = datetime.datetime.now()

In [66]:
instance2 - instance1

datetime.timedelta(seconds=5, microseconds=719244)

In [12]:
range(start, end)

TypeError: 'datetime.datetime' object cannot be interpreted as an integer

In [23]:
curr_date = curr_date.replace(month = 12, year = 1)

In [32]:
13%12

1

In [78]:
s = datetime.datetime.now().second
ms = datetime.datetime.now().microsecond
print(s,ms)

26 917177


In [84]:
curr_date = after_call_time = datetime.datetime.strptime("9-1851", "%m-%Y")
end_date = datetime.datetime.now()
end_date - curr_date

datetime.timedelta(days=61283, seconds=50670, microseconds=559690)

In [87]:
curr_date

datetime.datetime(1851, 9, 1, 0, 0)

In [88]:
after_call_time

datetime.datetime(1851, 9, 1, 0, 0)

In [89]:
after_call_time = after_call_time.replace(month = 5)

In [90]:
after_call_time

datetime.datetime(1851, 5, 1, 0, 0)

In [91]:
curr_date

datetime.datetime(1851, 9, 1, 0, 0)

In [81]:
s+ms*10e-7

26.917177

In [120]:
import sys
import json
import requests

API_SIGNUP_URL = 'https://developer.nytimes.com/get-started'

class ArchiveAPI():
    def __init__(self, key):
        if key is None:
            raise Exception('Must provide an API key. If you don\'t have one, go to \\ {} to sign up for one'.format(API_SIGNUP_URL))
        else:
            self.key = key
            
    def fetch_articles(self, month, year):
        """
        month: integer 1-12
        year : integer 1851-2019
        
        returns a response object
        """
        #Make sure inputs are good
        if not isinstance(month,int):
            raise ValueError('Month needs to be an integer')
        if not isinstance(year, int):
            raise ValueError('Year needs to be an integer')
        if month < 1 or month > 12:
            raise ValueError('Month needs to be 1-12')
        if year < 1851 or year > 2019:
            raise ValueError('Year needs to be 1851 - 2019')
        
        #Make call to API and get a response
        resp = requests.get('https://api.nytimes.com/svc/archive/v1/{}/{}.json?api-key={}'.format(year,month,self.key))
        try:
            if resp.status_code != 200:
                print("Error:")
                if resp.status_code == 401:
                    raise Exception('Unauthorized request, check api-key is set.')
                if resp.status_code == 429:
                    raise Exception('Too many requests. You reached your per minute or per day rate limit.')
            else:
                print("Response for {}/{}".format(month, year))
                return resp
        except Exception as exc:
            print('{} for {}/{}'.format(exc, month, year))
            
    def fetch_all_articles(self):
        """
        Returns a list of all responses from 1851 to the present month.
        """
        responses = []
        
        #New York Times's first issue was 9-18-1851
        curr_date = after_call_time = datetime.datetime.strptime("9-1851", "%m-%Y")
        end_date = datetime.datetime.now()
        print('Got responses for:\n')
        while curr_date <= end_date:
            month = curr_date.month
            year = curr_date.year
            try:
                #Make sure you've waited at least 6 seconds to make another call.
                time_since_last_call = (datetime.datetime.now() - after_call_time).total_seconds()
                if time_since_last_call < 6:
                    to_wait = 6 - time_since_last_call
                    time.sleep(to_wait)
                response = self.fetch_articles(month,year)
                after_call_time = datetime.datetime.now() 
                print('\t{}/{}'.format(month,year))
            except Exception as exc:
                print('Exception raised for {}/{}:\n{}'.format(month,year,exc))
            responses.append(response)
            #Execute API call
            #Get API call into pandas dataframe
            #Update date
            month += 1
            if month % 12 == 1:
                year += 1
                month = 1
            curr_date = curr_date.replace(month = month, year = year)
        return responses

        
        
    def fetch_articles_in_range(self,month_start,year_start,month_end, year_end):
        """
        Returns a list of all responses from 1851 to the present month.
        """
        responses = []
        
        curr_date = after_call_time = datetime.datetime.strptime("{}-{}".format(month_start,year_start), "%m-%Y")
        end_date = datetime.datetime.strptime("{}-{}".format(month_end,year_end), "%m-%Y")
        print('Got responses for:\n')
        while curr_date <= end_date:
            month = curr_date.month
            year = curr_date.year
            try:
                #Make sure you've waited at least 6 seconds to make another call.
                time_since_last_call = (datetime.datetime.now() - after_call_time).total_seconds()
                if time_since_last_call < 6:
                    to_wait = 6 - time_since_last_call
                    time.sleep(to_wait)
                response = self.fetch_articles(month,year)
                after_call_time = datetime.datetime.now() 
                print('\t{}/{}'.format(month,year))
            except Exception as exc:
                print('Exception raised for {}/{}:\n{}'.format(month,year,exc))
            responses.append(response)
            #Execute API call
            #Get API call into pandas dataframe
            #Update date
            month += 1
            if month % 12 == 1:
                year += 1
                month = 1
            curr_date = curr_date.replace(month = month, year = year)
        return responses
    
    ###TODO, make a new function which fetch_all_articles and fetch articles in range both use instead of
    ###reusing code.

        
        
        
#         responses = []
#         for month in np.arange(1,13):
#             for year in np.arange(1851,2020):
#                 time.sleep(6)
#                 try:
#                     responses = self.fetch_articles()
#                     print('\t{}/{}'.format(month,year))
#                 except Exception as exc:    
#                     print('Exception raised for {}/{}:\n{}'.format(month,year,exc))
                

#                 responses.append(resp)
                
    def resp_to_df(self, response):
        """
        Takes as input a single response object or a list of them and puts it into a dataframe
        """
        #If resp is a list, then turn each resp into a pandas dataframe and append them all.
        if isinstance(response, list):
            df = pd.DataFrame()
            for resp in response:
                article_metadata_array = resp.json()['response']['docs']
                df = df.append(pd.DataFrame(article_metadata_array))
        #Otherwise, turn the response into a pandas dataframe
        else:
            print("hello")
            article_metadata_array = response.json()['response']['docs']
            df = pd.DataFrame(article_metadata_array)
        return df
        
                

    def json_to_dataframe(self, json_file):
        """
        json_file:  a .json file which has been pulled from the Archive API and serialized in JSON format.
        """
        with open(json_file) as json_file:  
            data = json.load(json_file)
        return pd.DataFrame.from_dict(data['docs'])

    

# if __name__ == '__main__':
#     print(sys.argv)
#     if len(sys.argv) != 4:
#         raise IOError('User must specify API key, month, and year')
#     API_KEY,MONTH,YEAR = sys.argv[1:]
#     #TODO check that inputs are valid.
#     archiveAPI = ArchiveAPI(API_KEY)
#     articles = archiveAPI.fetch_articles(MONTH, YEAR)

#     #TODO allow user to specify output dir
#     with open('response.json', 'w') as outfile:
#         json.dump(articles.json()['response'], outfile)


### TODO Write TEST

In [151]:
# MONTH, YEAR = 6,2019
archiveAPI = ArchiveAPI(API_KEY)

In [ ]:
start = time.time()
all_articles = archiveAPI.fetch_all_articles()
end = time.time()
print("Took {} seconds".format(end - start))

Got responses for:

Response for 9/1851
	9/1851
Response for 10/1851
	10/1851
Response for 11/1851
	11/1851
Response for 12/1851
	12/1851
Response for 1/1852
	1/1852
Response for 2/1852
	2/1852
Response for 3/1852
	3/1852
Response for 4/1852
	4/1852
Response for 5/1852
	5/1852
Response for 6/1852
	6/1852
Response for 7/1852
	7/1852
Response for 8/1852
	8/1852
Response for 9/1852
	9/1852
Response for 10/1852
	10/1852
Response for 11/1852
	11/1852
Response for 12/1852
	12/1852
Response for 1/1853
	1/1853
Response for 2/1853
	2/1853
Response for 3/1853
	3/1853
Response for 4/1853
	4/1853
Response for 5/1853
	5/1853
Response for 6/1853
	6/1853
Response for 7/1853
	7/1853
Response for 8/1853
	8/1853
Response for 9/1853
	9/1853
Response for 10/1853
	10/1853
Response for 11/1853
	11/1853
Response for 12/1853
	12/1853
Response for 1/1854
	1/1854
Response for 2/1854
	2/1854
Response for 3/1854
	3/1854
Response for 4/1854
	4/1854
Response for 5/1854
	5/1854
Response for 6/1854
	6/1854
Response f

In [ ]:
#I want to see if this overwrites the old all_articles.p
start = end
pickle.dump(all_articles, open('all_articles.p', 'wb'))
end = time.time()
print("Took {} seconds".format(end - start))

In [ ]:
start = end
pickle.dump(all_articles, open('all_articles_new.p', 'wb'))
end = time.time()
print("Took {} seconds".format(end - start))

In [ ]:
start = end
df = archiveAPI.resp_to_df(all_articles)
end = time.time()
print("Took {} seconds".format(end - start))

In [ ]:
print(time.time())

In [ ]:
finish = datetime.datetime.now()
print(finish)

In [106]:
sys.getsizeof(articles)

56

In [53]:
n_0 = parser.parse(df.iloc[0]['pub_date'])

In [54]:
n_1000 = parser.parse(df.iloc[1000]['pub_date'])

In [64]:
def non_decreasing(L):
    print(len(L),len(L[1:]))
    return all(x<=y for x, y in zip(L, L[1:]))
non_decreasing(df['pub_date'])

15808 15807


False

In [46]:
datetime.datetime.strptime(df.iloc[0]['pub_date'],"%Y-%m-%dT%H:%M:%S%z")

datetime.datetime(2000, 1, 1, 0, 0, tzinfo=datetime.timezone.utc)

In [70]:
n_articles = articles.json()['response']['meta']['hits']
n_articles

7904

In [92]:
article_metadata_array = articles.json()['response']['docs']

In [16]:
columns = list(article_metadata_array[-1].keys())
columns

['web_url',
 'snippet',
 'lead_paragraph',
 'abstract',
 'print_page',
 'blog',
 'source',
 'multimedia',
 'headline',
 'keywords',
 'pub_date',
 'document_type',
 'news_desk',
 'section_name',
 'subsection_name',
 'byline',
 'type_of_material',
 '_id',
 'word_count',
 'slideshow_credits']

In [93]:
df = pd.DataFrame(article_metadata_array)

In [98]:
df.memory_usage().sum()

552128

In [105]:
df['word_count'].memory_usage()

26368

In [100]:
pwd

'/home/crytting/nytAPI'

In [17]:
df = pd.DataFrame(columns = columns)
start= time.time()
for article_metadata in article_metadata_array:
    df = df.append(article_metadata, ignore_index=True)
print('Took {} seconds'.format(time.time() - start))
df.iloc[0]

Took 67.363849401474 seconds


web_url              https://www.nytimes.com/2000/01/01/news/vision...
snippet              YOUNG, hip and smart, Casey Collier seems to g...
lead_paragraph       YOUNG, hip and smart, Casey Collier seems to g...
abstract             American teenagers feel pressure to succeed at...
print_page                                                          22
blog                                                                []
source                                              The New York Times
multimedia                                                          []
headline             {'main': 'A Generation's Anthem: 'Smells Like ...
keywords             [{'name': 'subject', 'value': 'CHILDREN AND YO...
pub_date                                          2000-01-01T00:00:00Z
document_type                                                  article
news_desk                                               The Millennium
section_name                                                      None
subsec

In [20]:
df.head()

web_url  \
0  https://www.nytimes.com/2000/01/01/news/vision...   
1  https://www.nytimes.com/2000/01/01/world/yelts...   
2  https://www.nytimes.com/2000/01/01/news/vision...   
3  https://www.nytimes.com/2000/01/01/arts/dance-...   
4  https://www.nytimes.com/2000/01/01/world/yelts...   

                                             snippet  \
0  YOUNG, hip and smart, Casey Collier seems to g...   
1  If Boris N. Yeltsin really meant it about bein...   
2  To: Marcy  From: Britanny  Videotex, 6/6/2025 ...   
3  The glorious athletes of Eliot Feld's ''Aurora...   
4  President Boris N. Yeltsin's resignation today...   

                                      lead_paragraph  \
0  YOUNG, hip and smart, Casey Collier seems to g...   
1  If Boris N. Yeltsin really meant it about bein...   
2  To: Marcy From: Britanny Videotex, 6/6/2025 (a...   
3  The glorious athletes of Eliot Feld's ''Aurora...   
4  President Boris N. Yeltsin's resignation today...   

                                            abstract print_page blog  \
0  American teenagers feel pressure to succeed at...         22   []   
1  Many Moscovites are happy or seem not to care ...         18   []   
2  Phil Patton article gives transcript of a 2025...         27   []   
3  Jennifer Dunning reviews Eliot Feld Ballet's p...         10   []   
4  Russian stock prices rise to their highest lev...         19   []   

               source multimedia  \
0  The New York Times         []   
1  The New York Times         []   
2  The New York Times         []   
3  The New York Times         []   
4  The New York Times         []   

                                            headline  \
0  {'main': 'A Generation's Anthem: 'Smells Like ...   
1  {'main': 'Yeltsin Leaves Russians Glad or Unin...   
2  {'main': 'Party Like It's 1999? That's So, Lik...   
3  {'main': 'Two Idealized Worlds With Contrastin...   
4  {'main': 'Heartened Investors Give Stock Marke...   

                                            keywords              pub_date  \
0  [{'name': 'subject', 'value': 'CHILDREN AND YO...  2000-01-01T00:00:00Z   
1  [{'name': 'persons', 'value': 'YELTSIN, BORIS ...  2000-01-01T00:00:00Z   
2  [{'name': 'subject', 'value': 'SPACE'}, {'name...  2000-01-01T00:00:00Z   
3  [{'name': 'organizations', 'value': 'FELD, ELI...  2000-01-01T00:00:00Z   
4  [{'name': 'persons', 'value': 'PUTIN, VLADIMIR...  2000-01-01T00:00:00Z   

  document_type               news_desk section_name subsection_name  \
0       article          The Millennium         None            None   
1       article            Foreign Desk        World            None   
2       article          The Millennium         None            None   
3       article  The Arts/Cultural Desk         Arts            None   
4       article            Foreign Desk        World            None   

                                              byline type_of_material  \
0  {'person': [{'organization': '', 'role': 'repo...             News   
1  {'person': [{'organization': '', 'role': 'repo...             News   
2  {'person': [{'organization': '', 'role': 'repo...             News   
3  {'person': [{'organization': '', 'role': 'repo...           Review   
4  {'person': [{'organization': '', 'role': 'repo...             News   

                        _id word_count slideshow_credits  
0  4fd1f22e8eb7c8105d7496fb       1063              None  
1  4fd203338eb7c8105d768e8e        989              None  
2  4fd203338eb7c8105d768e94        803              None  
3  4fd203338eb7c8105d768e9d        337              None  
4  4fd205c88eb7c8105d76e419        294              None

In [29]:
article_metadata_array

[{'web_url': 'https://www.nytimes.com/2000/01/01/news/visions-identity-a-generation-s-anthem-smells-like-teen-pressure.html',
  'snippet': "YOUNG, hip and smart, Casey Collier seems to glide from one peak to the next, knocking out A's, winning student council elections and starring in the school play.    She is an 18-year-old with a dazzling future. So why does she fret?    ''I feel o...",
  'lead_paragraph': "YOUNG, hip and smart, Casey Collier seems to glide from one peak to the next, knocking out A's, winning student council elections and starring in the school play. She is an 18-year-old with a dazzling future. So why does she fret? ''I feel overwhelmed -- I feel like, 'Oh my gosh, this stress,' '' said Miss Collier, a senior at Shawnee Mission North High School in Kansas, outside Kansas City. ''The other night, I wondered, 'Is it possible to have a nervous breakdown at age 18?' ''",
  'abstract': 'American teenagers feel pressure to succeed at dawn of new century; photos (M)',
  '

In [32]:
start = time.time()
article_metadata_array_flattened = (flatten(d) for d in article_metadata_array)
print('Took {} seconds'.format(time.time() - start))

Took 0.000164031982421875 seconds


In [98]:
article_metadata_array[:5]

[{'web_url': 'https://query.nytimes.com/gst/abstract.html?res=9D0CEEDF1438E334BC4953DFB7678389649FDE',
  'snippet': "MR. CORWIN AND THE GARDINER CLAIM.- Mr. CORWIN has gone to Ohio, it is said by a correspondent of the Baltimore Sun. to east his vote for the Whig 'candidate for the Presidency. It is Mr. C.'s purpose, if a suitable opportunity presents itself, to...",
  'lead_paragraph': "MR. CORWIN AND THE GARDINER CLAIM.- Mr. CORWIN has gone to Ohio, it is said by a correspondent of the Baltimore Sun. to east his vote for the Whig 'candidate for the Presidency. It is Mr. C.'s purpose, if a suitable opportunity presents itself, to vindicate him self before his former constituents from the charges of Dr. OLDs as to the GARDINER claim.",
  'abstract': None,
  'print_page': '1',
  'blog': [],
  'source': 'The New York Times',
  'multimedia': [],
  'headline': {'main': 'Front Page 2 -- No Title', 'kicker': '1'},
  'keywords': [],
  'pub_date': '1852-11-01T00:03:58Z',
  'document_type': 'ar

In [96]:
df_2.iloc[1]['byline.person']

[{'organization': '', 'role': 'reported', 'rank': 1}]

In [107]:
df_2['byline.person'].astype(str).unique()

array(['nan', "[{'organization': '', 'role': 'reported', 'rank': 1}]",
       "[{'organization': '', 'role': 'reported', 'rank': 1}, {'organization': '', 'role': 'reported', 'rank': 2}]",
       '[]',
       "[{'firstname': 'R.', 'middlename': 'N.', 'lastname': 'H', 'rank': 1, 'role': 'reported', 'organization': ''}]",
       "[{'firstname': 'J.', 'middlename': 'S.', 'lastname': 'SCOFIELD', 'rank': 1, 'role': 'reported', 'organization': ''}, {'organization': '', 'role': 'reported', 'rank': 2}]",
       '[{\'organization\': \'\', \'role\': \'reported\', \'rank\': 1, \'firstname\': "Dan\'l", \'lastname\': \'WEBSTER\'}]',
       "[{'organization': '', 'role': 'reported', 'rank': 1, 'firstname': 'L.', 'lastname': 'STEVENS'}]",
       "[{'organization': '', 'role': 'reported', 'rank': 1, 'firstname': 'Oration', 'lastname': 'REV'}]",
       "[{'firstname': 'Albert', 'middlename': 'H.', 'lastname': 'Nicolay', 'rank': 1, 'role': 'reported', 'organization': ''}]",
       "[{'firstname': 'X.', '

In [99]:
article_metadata_array_copy = np.copy(article_metadata_array)

In [104]:
orig_person_dic = article_metadata_array_copy[1]['byline']['person']
extra_dic_copy = extra_dic

[{'organization': '', 'role': 'reported', 'rank': 1}]

In [26]:
MONTH, YEAR = 9,2001
archiveAPI = ArchiveAPI(API_KEY)
responses = []
for i in np.arange(1,3):
    responses.append(archiveAPI.fetch_articles(i, YEAR))

Response for 1/2001
Response for 2/2001


In [47]:
responses[0].json() == data[0]

True

In [40]:
responses_json_strings = [response.json() for response in responses]

In [42]:
#TODO allow user to specify output dir
with open('responses.json', 'w') as outfile:
    json.dump(responses_json_strings, outfile)


In [43]:
with open('responses.json') as json_file:

    data = json.load(json_file)


In [44]:
data

[{'copyright': 'Copyright (c) 2013 The New York Times Company.  All Rights Reserved.',
  'response': {'meta': {'hits': 7736},
   'docs': [{'web_url': 'https://www.nytimes.com/2001/01/01/sports/sports-of-the-times-count-one-more-vote-for-the-ravens-defense.html',
     'snippet': "IN his moment of triumph yesterday, Brian Billick used the postgame podium to toss one final shot at Al Groh, the departed Jets head coach. Before the Jets' game against Baltimore a week earlier, Groh had been sarcastic in praising the Ravens' def...",
     'lead_paragraph': "IN his moment of triumph yesterday, Brian Billick used the postgame podium to toss one final shot at Al Groh, the departed Jets head coach. Before the Jets' game against Baltimore a week earlier, Groh had been sarcastic in praising the Ravens' defense, telling members of the news media how the Jets didn't have a chance. Yesterday, in the wake of the Ravens' 21-3 victory over Denver, Billick was asked how the Ravens' offense would attack th

In [12]:
API_KEY = 'v2wsp3yB5OWqhGf99uzEpFaGwddFnyCh'
API_SIGNUP_URL = 'https://developer.nytimes.com/get-started'

class ArchiveAPI():
    def __init__(self, key):
        if key is None:
            raise Exception('Must provide an API key. \
            If you don\'t have one, go to {} to sign up for one'\
                            .format(API_SIGNUP_URL))
        else:
            self.key = key
            
    def fetch_articles(self, month, year):
        """
        month: integer 1-12
        year : integer 1851-2019
        
        returns a request object
        """
        
        resp = requests.get('https://api.nytimes.com/svc/archive/v1/{}/{}.json?api-key={}'.format(year,month,self.key))
        print('inside fetch_articles')
        return resp
        try:
            if resp.status_code != 200:
                print("Error: resp.status_code = {}".format(resp.status_code))
                if resp.status_code == 401:
                    raise Exception('Unauthorized request, check\
                    api-key is set.')
                if resp.status_code == 429:
                    raise Exception('Too many requests. You reached \
                    your per minute or per day rate limit.')
            else: 
                return resp
        except:
            print('No Resp')
        
                            
        
        



In [20]:
if __name__ == '__main__':
    archiveAPI = ArchiveAPI(API_KEY)
    articles = archiveAPI.fetch_articles(9, 2001)
    
    

    
#     sys.argv.append('hello')
#     print(sys.argv)
#     api = ArchiveAPI('key')
#     api.fetch_articles('asdf','asdf')

inside fetch_articles


In [34]:
articles.json().keys()

dict_keys(['copyright', 'response'])

In [36]:
articles.json()['response']

{'meta': {'hits': 8297},
 'docs': [{'web_url': 'https://www.nytimes.com/2001/09/01/arts/edward-rivera-62-writer-and-teacher.html',
   'snippet': "Edward Rivera, the author of the autobiographical novel ''Family Installments: Memoirs of Growing Up Hispanic'' and an assistant professor at City College of New York, died on Aug. 25 in Manhattan, where he lived. He was 62.    The cause was a hea...",
   'lead_paragraph': "Edward Rivera, the author of the autobiographical novel ''Family Installments: Memoirs of Growing Up Hispanic'' and an assistant professor at City College of New York, died on Aug. 25 in Manhattan, where he lived. He was 62. The cause was a heart attack, said his brother Richard.",
   'abstract': 'Edward Rivera, author of autobiographical novel Family Installments: Memoirs of Growing Up Hispanic, and assistant professor at City College of New York, dies at age 62; photo (S)',
   'print_page': '15',
   'blog': [],
   'source': 'The New York Times',
   'multimedia': [],
   '

In [33]:
with open('response.json', 'w') as outfile:
    json.dump(articles.json()['response'], outfile)
# articles.json()['response']

In [22]:
for key, value in articles.headers.items():
    print ('Key: {} \t Value: {}'.format(key, value))

# type(resp.json())

# resp.json()['response'].keys()

# len(resp.json()['response']['docs'])

resp.json()['response']['docs'][0]['web_url']

Key: Date 	 Value: Thu, 28 Mar 2019 03:10:27 GMT
Key: Content-Type 	 Value: application/json
Key: Transfer-Encoding 	 Value: chunked
Key: Connection 	 Value: keep-alive
Key: x-amz-id-2 	 Value: M9e3iGVnPDVLTm60zfaYBI7RO6qIULs564GUMcQIporbVT7oYhIgDZ442rNKJatmHYJHlPs1GqE=
Key: x-amz-request-id 	 Value: 6F2C0AADA6654C5C
Key: Last-Modified 	 Value: Thu, 01 Jun 2017 19:32:02 GMT
Key: ETag 	 Value: "fc608e5d0d5c25a83e7de9278e6e26c7"
Key: Cache-Control 	 Value: max-age=43200
Key: Expires 	 Value: Fri, 02 Jun 2017 07:32:01 GMT
Key: Server 	 Value: AmazonS3
Key: Content-Encoding 	 Value: gzip
Key: Accept-Ranges 	 Value: bytes
Key: Via 	 Value: 1.1 varnish
Key: Age 	 Value: 1
Key: X-Served-By 	 Value: cache-bwi5043-BWI
Key: X-Cache 	 Value: MISS
Key: X-Cache-Hits 	 Value: 0
Key: X-Timer 	 Value: S1553742627.554721,VS0,VE1079
Key: Vary 	 Value: Origin, Access-Control-Request-Headers, Access-Control-Request-Method, Accept-Encoding
Key: Access-Control-Allow-Origin 	 Value: *
Key: Access-Control-All

NameError: name 'resp' is not defined

In [3]:
with open('response.json') as json_file:  
    data = json.load(json_file)


In [6]:
data.keys()

dict_keys(['meta', 'docs'])

In [8]:
data['meta']

{'hits': 6977}

In [19]:
keys = data['docs'][0].keys()

dict_keys(['web_url', 'snippet', 'lead_paragraph', 'print_page', 'blog', 'source', 'multimedia', 'headline', 'keywords', 'pub_date', 'document_type', 'news_desk', 'section_name', 'byline', 'type_of_material', '_id', 'word_count', 'score', 'uri'])

In [17]:
for key, value in data['docs'][0].items():
    print("Key = {}, Value = {}".format(key, value))

Key = web_url, Value = https://www.nytimes.com/2019/01/02/obituaries/daryl-dragon-dead.html
Key = snippet, Value = He and his wife, Toni Tennille, were one of the most successful hit-making combinations of the 1970s. Their “Love Will Keep Us Together” went to No. 1.
Key = lead_paragraph, Value = He and his wife, Toni Tennille, were one of the most successful hit-making combinations of the 1970s. Their “Love Will Keep Us Together” went to No. 1.
Key = print_page, Value = 10
Key = blog, Value = []
Key = source, Value = The New York Times
Key = multimedia, Value = [{'rank': 0, 'subtype': 'xlarge', 'caption': None, 'credit': None, 'type': 'image', 'url': 'images/2019/01/03/obituaries/03DRAGON1-print/merlin_148690920_b809ab8a-e519-4e75-8770-9d43fe082f7c-articleLarge.jpg', 'height': 446, 'width': 600, 'legacy': {'xlarge': 'images/2019/01/03/obituaries/03DRAGON1-print/merlin_148690920_b809ab8a-e519-4e75-8770-9d43fe082f7c-articleLarge.jpg', 'xlargewidth': 600, 'xlargeheight': 446}, 'subType': 

In [51]:
df = pd.DataFrame.from_dict(data['docs'])

_id blog  \
0     5c2d52db3a125f5075c029ae   []   
1     5c2d38833a125f5075c02974   []   
2     5c2cee413a125f5075c028db   []   
3     5c2d02703a125f5075c028fd   []   
4     5c2d03dd3a125f5075c02901   []   
5     5c2da4e73a125f5075c02a12   []   
6     5c2cb0933a125f5075c0286f   []   
7     5c2e2f0f3a125f5075c02b01   []   
8     5c2d3b713a125f5075c0297f   []   
9     5c2af8393a125f5075c026c9   []   
10    5c2b01e63a125f5075c026d3   []   
11    5c2ab6b83a125f5075c02693   []   
12    5c2abdb83a125f5075c0269d   []   
13    5c2ba7a53a125f5075c0275b   []   
14    5c2ac5f13a125f5075c026a3   []   
15    5c2cd8e83a125f5075c028aa   []   
16    5c2d220f3a125f5075c02940   []   
17    5c2e38bf3a125f5075c02b1e   []   
18    5c2ddd313a125f5075c02a6e   []   
19    5c2b16fe3a125f5075c026df   []   
20    5c2bcaef3a125f5075c0277f   []   
21    5c2c39dc3a125f5075c027d1   []   
22    5c2bca483a125f5075c0277e   []   
23    5c2c99b63a125f5075c02851   []   
24    5c2d35393a125f5075c0296d   []   
25    5c2bac343a125f5075c02764   []   
26    5c2ddd2f3a125f5075c02a6d   []   
27    5c2e611e3a125f5075c02b86   []   
28    5c2e62b03a125f5075c02b8a   []   
29    5c2e608a3a125f5075c02b84   []   
...                        ...  ...   
6947  5c5280d73a125f5075c073b9   []   
6948  5c5392be3a125f5075c076e9   []   
6949  5c5392c43a125f5075c076ea   []   
6950  5c5392d23a125f5075c076ef   []   
6951  5c5326f23a125f5075c07564   []   
6952  5c52fd443a125f5075c074ec   []   
6953  5c53adab3a125f5075c07735   []   
6954  5c53e9463a125f5075c077b0   []   
6955  5c52c7393a125f5075c07456   []   
6956  5c5312b13a125f5075c0752b   []   
6957  5c53044b3a125f5075c074fe   []   
6958  5c52c3a23a125f5075c07442   []   
6959  5c5274e83a125f5075c073b2   []   
6960  5c53242d3a125f5075c07560   []   
6961  5c530dfa3a125f5075c07520   []   
6962  5c53458b3a125f5075c075d7   []   
6963  5c53066e3a125f5075c07502   []   
6964  5c53451b3a125f5075c075d4   []   
6965  5c5333f03a125f5075c07588   []   
6966  5c5333f03a125f5075c07588   []   
6967  5c535cb23a125f5075c0764c   []   
6968  5c53d2713a125f5075c07778   []   
6969  5c538d533a125f5075c076db   []   
6970  5c52ca953a125f5075c07465   []   
6971  5c53890e3a125f5075c076d3   []   
6972  5c535cdf3a125f5075c0764e   []   
6973  5c536fe63a125f5075c0767c   []   
6974  5c53e0a03a125f5075c07793   []   
6975  5c53fc883a125f5075c077de   []   
6976  5c52c7233a125f5075c0744b   []   

                                                 byline document_type  \
0     {'original': 'By NEIL GENZLINGER', 'person': [...       article   
1     {'original': 'By CHRISTINA ANDERSON', 'person'...       article   
2     {'original': 'By TRIP GABRIEL', 'person': [{'f...       article   
3     {'original': None, 'person': None, 'organizati...       article   
4     {'original': None, 'person': None, 'organizati...       article   
5     {'original': 'By GABE COHN', 'person': [{'firs...       article   
6     {'original': 'By KAI SCHULTZ and AYESHA VENKAT...       article   
7     {'original': 'By PHILIP GALANES', 'person': [{...       article   
8     {'original': 'By WHITSON GORDON', 'person': [{...       article   
9     {'original': None, 'person': None, 'organizati...       article   
10    {'original': 'By LAUREN MESSMAN', 'person': [{...       article   
11    {'original': None, 'person': None, 'organizati...       article   
12    {'original': None, 'person': None, 'organizati...       article   
13    {'original': 'By PAUL KRUGMAN', 'person': [{'f...       article   
14    {'original': 'By MOTOKO RICH and DAVID E. SANG...       article   
15    {'original': 'By JULIE HIRSCHFELD DAVIS and MI...       article   
16    {'original': 'By MARTHA SCHWENDENER', 'person'...       article   
17    {'original': 'By ADAM NOSSITER', 'person': [{'...       article   
18    {'original': 'By ERNESTO LONDOÑO', 'person': [...       article   
19    {'original': 'By RACHEL NUWER', 'person': [{'f...       article   
20    {'original': 'By EMMA G. FITZSIMMONS', 'person...       article   
21